In [2]:
import pandas as pd
import geopandas as gpd
import numpy as np
import folium
from geopandas import GeoDataFrame
import random
from shapely.geometry import Point
from folium import plugins, FeatureGroup, LayerControl, Map, Marker
from folium.plugins import HeatMap, FastMarkerCluster

# Funcion generadora de puntos aleatorios
Inicialmente era una funcion que me permitia sacar un punto aleatorio contenido en un poligono. Tuve un error que no pude solucionar por lo que opte sacar ese if (que lo van a ver en este link https://gis.stackexchange.com/questions/207731/how-to-generate-random-coordinates-in-a-multipolygon-in-python/207774#207774). Lo que si es posible es que haya gente cerca de California pero en el medio del mar (se aprecia mejor esto en el heatmap y en el clustered map). Esto lo hice para poder jugar con las locations (lat, long), dato que no estaba en la df original.

In [3]:
# https://gis.stackexchange.com/questions/207731/how-to-generate-random-coordinates-in-a-multipolygon-in-python/207774#207774
# Elimine la condicion de que este adentro del poligono, no pude solucionar ese error (es posible que me figuren personas en el medio del mar, por ejemplo)

random.seed(2019)
def generate_random(number, polygon):
    list_of_points = []
    minx, miny, maxx, maxy = polygon.bounds
    counter = 0
    while counter < number:
        pnt = Point(random.uniform(minx, maxx), random.uniform(miny, maxy))
        list_of_points.append(pnt)
        counter += 1
    return list_of_points

# Lectura GeoJson a geopandas dataframe
Esto me sirve para poder mergear con las dataframes que contienen los datos con los que voy a interactuar.

In [4]:
df_counties = gpd.read_file("ca_map.geo.json")
df_counties=df_counties[["name","geometry"]]
df_counties.columns=["county", "geometry"]
df_counties.head()

county                                           geometry
0    Alameda  (POLYGON ((-122.312934 37.897333, -122.28848 3...
1     Alpine  POLYGON ((-120.072392 38.702767, -119.964948 3...
2     Amador  POLYGON ((-121.027262 38.489252, -121.027406 3...
3      Butte  POLYGON ((-121.879249 39.303608, -121.908312 3...
4  Calaveras  POLYGON ((-120.876047 38.028894, -120.918749 3...

In [5]:
dict_counties=dict(zip(df_counties.county, df_counties.geometry)) #Para generar counties y locations arbitrariamente 

# Lectura del data set
Leo el data set, inicialmente tenia unas locations (algunos casos no contemplaban locations propias de california o de los Estados Unidos). Por lo que decidi dropearlos y generarlos aleatoriamente (como si las personas estuviesen dispersas a lo largo de California, en los distintos condados). Para cada uno de las personas y para cada condado perteneciente a esa persona, genere un punto geometrico (latitud, longitud).
Traté algunos outliers y missings pertenecientes a altura, edad e ingresos. Tambien aplique el tratamiento de missings para smokes. 

In [135]:
df = pd.read_csv("profiles.csv")
del df["location"]
np.random.seed(2019)
df['county'] = np.random.choice(list(df_counties["county"]), len(df))
list_points=[]
for c in list(df["county"]):
    list_points.append(generate_random(1, dict_counties[c])[0])
df["Point"]= list_points
df["lat"] = [p.y for p in list(df["Point"])]
df["long"] =  [p.x for p in list(df["Point"])]
df["height"] = df["height"].fillna(round(df["height"].mean(),0))
df["height"]=[round(df["height"].mean(),0) if x<50 else x for x in list(df["height"])]
df["height"]=df["height"]+100
df["age"]=[round(df["age"].mean(),0) if x>80 else x for x in list(df["age"])]
df["income"]=[0 if x==-1 else x for x in list(df["income"])]
df=df.fillna(({'smokes':'missing'}))
#df["location"] = df["location"].replace(dictionary)
#df = df.dropna(subset = ["location"])
#df = df[df['location'].str.contains("california")]
#df["county"], df["state"] = zip(*df["location"].str.split(",").tolist()) 
#del df["state"]
#del df["location"]
#df["county"]=[x if x not in dict_wiki else dict_wiki[x] for x in list(df["county"])]
#keys_usa = ["albany", 'ashland','North hollywood'] + list(set(df["county"]) - set(df_counties.county))
#values_usa = [np.nan for x in range(len(keys_usa))]
#dict_usa = dict(zip(keys_usa, values_usa))
#df["county"] = df["county"].replace(dict_usa)
df.head()

age       body_type               diet    drinks      drugs  \
0  22.0  a little extra  strictly anything  socially      never   
1  35.0         average       mostly other     often  sometimes   
2  38.0            thin           anything  socially        NaN   
3  23.0            thin         vegetarian  socially        NaN   
4  29.0        athletic                NaN  socially      never   

                           education  \
0      working on college/university   
1              working on space camp   
2     graduated from masters program   
3      working on college/university   
4  graduated from college/university   

                                              essay0  \
0  about me:<br />\n<br />\ni would love to think...   
1  i am a chef: this is what that means.<br />\n1...   
2  i'm not ashamed of much, but writing public te...   
3          i work in a library and go to school. . .   
4  hey how's it going? currently vague on the pro...   

                                              essay1  \
0  currently working as an international agent fo...   
1  dedicating everyday to being an unbelievable b...   
2  i make nerdy software for musicians, artists, ...   
3          reading things written by old dead people   
4                         work work work work + play   

                                              essay2  \
0  making people laugh.<br />\nranting about a go...   
1  being silly. having ridiculous amonts of fun w...   
2  improvising in different contexts. alternating...   
3  playing synthesizers and organizing books acco...   
4  creating imagery to look at:<br />\nhttp://bag...   

                                              essay3     ...      \
0  the way i look. i am a six foot half asian, ha...     ...       
1                                                NaN     ...       
2  my large jaw and large glasses are the physica...     ...       
3                  socially awkward but i do my best     ...       
4            i smile a lot and my inquisitive nature     ...       

                                   religion sex  \
0     agnosticism and very serious about it   m   
1  agnosticism but not too serious about it   m   
2                                       NaN   m   
3                                       NaN   m   
4                                       NaN   m   

                                 sign     smokes  \
0                              gemini  sometimes   
1                              cancer         no   
2  pisces but it doesn&rsquo;t matter         no   
3                              pisces         no   
4                            aquarius         no   

                                              speaks     status     county  \
0                                            english     single   Tuolumne   
1  english (fluently), spanish (poorly), french (...     single     Placer   
2                               english, french, c++  available     Shasta   
3                           english, german (poorly)     single  San Mateo   
4                                            english     single   Mariposa   

                                          Point        lat        long  
0  POINT (-119.8788513114477 37.65585054250089)  37.655851 -119.878851  
1   POINT (-120.5545092814848 39.0183555412338)  39.018356 -120.554509  
2  POINT (-122.8581695683933 40.76584207579425)  40.765842 -122.858170  
3  POINT (-122.4247106172757 37.12833689697408)  37.128337 -122.424711  
4   POINT (-119.457781998375 37.49576248745986)  37.495762 -119.457782  

[5 rows x 34 columns]

# Agregaciones
Realizo agregaciones para interactuar con edad, altura e ingresos. Luego mergeo con el dataframe que contiene los condados.

In [30]:
df_agg = df.groupby("county").mean()
df_agg_age = df_agg.reset_index()[["county", "age"]]
df_agg_height = df_agg.reset_index()[["county", "height"]]
df_merged_age = df_counties.merge(df_agg_age, on='county')
df_merged_age.columns=["name", "geometry", "age"]
df_merged_height = df_counties.merge(df_agg_height, on='county')
df_merged_height.columns=["name", "geometry", "height"]
df_merged_income = df_counties.merge(df.groupby("county").mean().reset_index()[["county","income"]], on='county')
df_merged_income.columns=["name", "geometry", "income"]

# Ploteo de mapas para las agregaciones
Ploteo las agregaciones correspondiente a edad promedio, altura promedio e ingresos promedio. Genero un regular polygon marker para cada row de la agregación, la cual estara en el centroide del poligono. Al hacer clic sobre el mismo se podra ver información relativa a dicha instancia de la agregación que la contiene. 

In [17]:
mapa_age = folium.Map(location=[37.866, -119.597],
                   tiles='Mapbox Bright', zoom_start=6)
    

folium.Choropleth(geo_data='california-counties.geojson', data=df_merged_age,
             columns=["name", "age"],
             key_on='feature.properties.name',
             fill_color='BuPu', fill_opacity=0.7, line_opacity=0.2,
             legend_name='Age (Avg.)').add_to(mapa_age)


for index, row in df_merged_age.iterrows():
    folium.RegularPolygonMarker(location=[row['geometry'].centroid.y, row['geometry'].centroid.x], radius=6, 
                         popup=folium.Popup("County:" + row["name"].replace(' ', '') + "\n Avg Age: "+ str(round(row["age"],2)))).add_to(mapa_age)

folium.LayerControl().add_to(mapa_age)

mapa_age

In [18]:
mapa_height = folium.Map(location=[37.866, -119.597],
                   tiles='Mapbox Bright', zoom_start=6)

folium.Choropleth(geo_data='california-counties.geojson', data=df_merged_height,
             columns=["name", "height"],
             key_on='feature.properties.name',
             fill_color='BuPu', fill_opacity=0.7, line_opacity=0.2,
             legend_name='Height (Avg.)').add_to(mapa_height)

for index, row in df_merged_height.iterrows():
    folium.RegularPolygonMarker(location=[row['geometry'].centroid.y, row['geometry'].centroid.x], radius=6, 
                         popup=folium.Popup("County:" + row["name"].replace(' ', '') + "\n Avg Height: "+ str(round(row["height"],2)))).add_to(mapa_height)


folium.LayerControl().add_to(mapa_height)

mapa_height

In [130]:
mapa_income = folium.Map(location=[37.866, -119.597],
                   tiles='Mapbox Bright', zoom_start=6)
    

folium.Choropleth(geo_data='california-counties.geojson', data=df_merged_income,
             columns=["name", "income"],
             key_on='feature.properties.name',
             fill_color='BuPu', fill_opacity=0.7, line_opacity=0.2,
             legend_name='Income (Avg.)').add_to(mapa_income)


for index, row in df_merged_income.iterrows():
    folium.RegularPolygonMarker(location=[row['geometry'].centroid.y, row['geometry'].centroid.x], radius=6, 
                         popup=folium.Popup("County:" + row["name"].replace(' ', '') + "\n Avg Income: "+ str(round(row["income"],2)))).add_to(mapa_income)

folium.LayerControl().add_to(mapa_income)

mapa_income

# Heat Map
Ploteo un heatmap sobre las posiciones de cada usuario de OkCupid.
Tomo una muestra del data set ya que con mas instancias el mapa no carga.

In [131]:
hmap = folium.Map(location=[37.866, -119.597], zoom_start=6)
subset_of_df = df.sample(n=30000)  
hm_wide = HeatMap( list(zip(subset_of_df.lat.values, subset_of_df.long.values)),
                   min_opacity=0.2,
                   radius=9, blur=15, 
                   max_zoom=1)

hmap.add_child(hm_wide)

# Clustered Map
Genero un clustered map, al hacer zoom se va "desclusterizando" y armandose nuevos clusters acorde al zoom seteado.
Tomo una muestra del data set ya que con mas instancias el mapa no carga.

In [134]:
#creating a map that's centered to our sample
subset_of_df = df.sample(n=30000)
some_map = folium.Map(location=[subset_of_df['lat'].mean(), 
                                subset_of_df['long'].mean()], 
                                zoom_start=5)

some_map.add_child(FastMarkerCluster(subset_of_df[['lat', 'long']].values.tolist()))
some_map

# Ploteo sobre la situación de "fumador" de la gente
La intención es plotear cuanta gente de cada situación (si fuma,no fuma, a veces, tratando de salir, cuando tomo) hay en cada condado.
Trabajo sobre una df nueva, eliminando los missings. Aplico el analisis sobre "no","sometimes","trying to quit","when drinking" y "yes".
Aplico on hot encoding para luego sumar y obtener cuantas personas tengo en cada situación para cada condado. 
Creo un diccionario para aplicar un ruido sobre el marker para que se muestren dispersos en el mapa. Creo otro diccionario para asignar un icon personalizado para cada situacion.
Itero y aplico cada uno de estos elementos de los diccionarios que cree en el marker.

In [34]:
df_smokes=df[df["smokes"]!="missing"][["county", "lat", "long", "smokes"]]

In [39]:
df_smokes_onehot=pd.merge(df_smokes[["county", "lat","long"]],pd.get_dummies(df_smokes["smokes"]), left_index=True, right_index=True).groupby("county").sum()[["no","sometimes","trying to quit","when drinking","yes"]].reset_index()
df_merged_smokes = df_counties.merge(df_smokes_onehot, on='county')
df_merged_smokes.columns = ["name","geometry","no","sometimes","trying to quit","when drinking","yes"]

In [128]:
dict_random=dict(zip(['sometimes', 'no', 'missing', 'when drinking', 'yes', 'trying to quit'], 
                     [0.0001,0.0004,0.0008,-0.0001,-0.0006,-0.0003]))
dict_icons = dict(zip(['sometimes', 'no', 'missing', 'when drinking', 'yes', 'trying to quit'], 
                     ['https://image.flaticon.com/icons/svg/188/188425.svg', 'https://image.flaticon.com/icons/svg/1655/1655732.svg',
                     'https://image.flaticon.com/icons/svg/1655/1655732.svg', 'https://cdn4.iconfinder.com/data/icons/stress-management-flat-relaxation/512/Alcoholism_addict-512.png',
                    'https://image.flaticon.com/icons/svg/1085/1085388.svg', 'https://image.flaticon.com/icons/svg/1686/1686605.svg']))


In [129]:
mapa_smokes = folium.Map(location=[37.866, -119.597],
                   tiles='Mapbox Bright', zoom_start=6)

folium.Choropleth(geo_data='california-counties.geojson', data=df_merged_smokes,
             columns=['name',  'no', 'sometimes', 'trying to quit', 'when drinking', 'yes'],
             key_on='feature.properties.name',
             fill_color='BuPu', fill_opacity=0.7, line_opacity=0.2).add_to(mapa_smokes)
for sit in ['sometimes', 'no', 'when drinking', 'yes', 'trying to quit']:
    for index, row in df_merged_smokes.iterrows():
        icon = folium.features.CustomIcon(dict_icons[sit], icon_size=(55,55))
        folium.Marker(location=[row['geometry'].centroid.y*(dict_random[sit]+1), 
                                              row['geometry'].centroid.x*(dict_random[sit]+1)], icon = icon,
                             popup=folium.Popup("County:" + row["name"].replace(' ', '') + "\n "+ sit+ ": "+ str(row[sit]))).add_to(mapa_smokes)


folium.LayerControl().add_to(mapa_smokes)

mapa_smokes

In [ ]:
#Ideas: Plotear markers personalizados para cada tipo (Podria ser para Carreras STEM y no STEM, podria ser para signos zodiacales..)